# GASS-PPI

## Section 0: Libraries, Global Variables, Utility Functions

In [48]:
import subprocess
import re
import numpy as np
from Bio.PDB import *

repository = "/Users/albertdarmawan/Documents/gass-ppi/"
current_directory = repository + "core/"
dataset_directory = repository + "dataset/benchmark5/structures/"
pdb_parser = PDBParser()

# List of PDB ID of protein complexes
# aa stands for Antibody-Antigen (in this case, Antibody is the receptor and Antigen is the ligand)
dbd5_aa_list = ["1AHW", "1BVK", "1DQJ", "1E6J", "1JPS", "1MLC", "1VFB", "1WEJ",
                              "2FD6", "2I25", "2VIS", "2VXT", "2W9E", "3EOA", "3HMX", "3MXW",
                              "3RVW", "4DN4", "4FQI", "4G6J", "4G6M", "4GXU", "3EO1", "3G6D",
                              "3HI6", "3L5W", "3V6Z", "1BGX"]

dbd5_aa_r_list = list(map(lambda x: x + "_r_u", dbd5_aa_list))
dbd5_aa_l_list = list(map(lambda x: x + "_l_u", dbd5_aa_list))
# example = pdb_parser.get_structure("1AHW_L", dataset_directory + "1AHW_l_u.pdb")
lha_dict = {
    "GLY":"CA",
    "ALA":"CB",
    "GLN":"CD",
    "GLU":"CD",
    "ILE":"CD1",
    "LEU":"CD1",
    "MET":"CE",
    "HIS":"CE1",
    "ASN":"CG",
    "ASP":"CG",
    "PRO":"CG",
    "VAL":"CG1",
    "THR":"CG2",
    "TRP":"CH2",
    "ARG":"CZ",
    "PHE":"CZ",
    "LYS":"NZ",
    "SER":"OG",
    "TYR":"OH",
    "CYS":"SG",
}


amino_acid_list = list(lha_dict.keys())

In [2]:
# Residue is represented as a Last Heavy Atom (LHA)
# Residue is a "gene" in genetic algorithms
# Individual is a list of residue
# 2 residue info, 1 chain info, 2 atom (lha) info
class Residue:
    def __init__(self, residue_name, residue_sequence_position, chain_name, lha_name, lha_coordinates):
        self.residue_name = residue_name
        self.residue_sequence_position = residue_sequence_position
        self.chain_name = chain_name
        self.lha_name = lha_name
        self.lha_coordinates = lha_coordinates

In [12]:
def euclidean_distance(coordinate_1, coordinate_2):
    """Euclidean Distance
    Given 3-dimensional coordinates of 2 atoms, calculate its Euclidean distance
    
    Parameters:
    coordinate_1 (1D NumPy Array): x,y,z coordinates of the first atom
    coordinate_2 (1D NumPy Array): x,y,z coordinates of the second atom
    
    Returns:
    float: The euclidean distance
    
    """
    return float(np.sqrt(((coordinate_1[0] - coordinate_2[0]) ** 2) +
                   ((coordinate_1[1] - coordinate_2[1]) ** 2) +
                   ((coordinate_1[2] - coordinate_2[2]) ** 2)))

In [4]:
# Using Sandro's script, generate a new PDB file with only its LHA
def generate_lha_file(pdb_id):
    pdb_file_name = pdb_id + ".pdb"
    new_thread = subprocess.run(["python", "pdb-preprocessing.py", repository + "TMalign/", pdb_file_name], capture_output=True, text=True)
    
generate_lha_file("1pme")

In [58]:
sample_pdb = pdb_parser.get_structure("3nos", repository + "TMalign/3nos.pdb")
# Only take the ATOM keyword (exclude the HETATM, hetero atom that is not inside standard amino acids)
residues_list = [residue for residue in sample_pdb.get_residues() if residue.get_resname() in amino_acid_list]

# From residues_list, create the lha_list
lha_list = [atom for residue in residues_list for atom in residue if atom.get_name() == lha_dict[residue.get_resname()]]
# From residues_list, create the ca_list
ca_list = [atom for residue in residues_list for atom in residue if atom.get_name() == "CA"]


/opt/anaconda3/envs/thesis/lib/python3.8/site-packages/Bio/PDB/StructureBuilder.py:89: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 7050.
  warnings.warn(
/opt/anaconda3/envs/thesis/lib/python3.8/site-packages/Bio/PDB/StructureBuilder.py:89: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 7124.
  warnings.warn(
/opt/anaconda3/envs/thesis/lib/python3.8/site-packages/Bio/PDB/StructureBuilder.py:89: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 7197.
  warnings.warn(
/opt/anaconda3/envs/thesis/lib/python3.8/site-packages/Bio/PDB/StructureBuilder.py:89: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 7450.
  warnings.warn(


In [22]:
def get_residue_list(pdb_id, reference_atom="lha"):
    """Get Residue List
    Given a PDB ID, get the list of residue
    
    Parameters:
    pdb_id (str): The PDB ID for the protein structure
    reference_atom (str): Reference atom used ("lha" or "ac")
    
    Returns:
    list: List of Residue object which constitutes the protein structure
    
    """
    residue_list = []
    pdb_directory_path = repository + "TMalign/" + pdb_id + "_lha.pdb" # TODO: Adjust this later
    pdb_structure = pdb_parser.get_structure(pdb_id, pdb_directory_path)
    for atom in pdb_structure.get_atoms():
        # Create a new Residue instance
        current_residue_name = atom.get_parent().get_resname()
        current_residue_sequence_position = atom.get_parent().get_full_id()[3][1]
        current_chain_name = atom.get_parent().get_parent().id
        current_lha_name = atom.get_name()
        current_lha_coordinates = atom.get_coord()
        current_atom = Residue(current_residue_name,
                               current_residue_sequence_position,
                               current_chain_name,
                               current_lha_name,
                               current_lha_coordinates)
        residue_list.append(current_atom)
    return residue_list

residue_3nos = get_residue_list("3nos")
print(type(residue_3nos))
print(len(residue_3nos))
for item in residue_3nos[:10]:
    print(item.residue_name)
    print(item.residue_sequence_position)
    print(item.chain_name)
    print(item.lha_name)
    print(item.lha_coordinates)

<class 'list'>
800
LYS
67
A
NZ
[ 9.963 -9.625 43.825]
PHE
68
A
CZ
[  4.961 -11.932  34.598]
PRO
69
A
CG
[ 9.418 -5.395 38.73 ]
ARG
70
A
CZ
[ 2.021  0.719 43.97 ]
VAL
71
A
CG1
[ 6.528  2.328 37.102]
LYS
72
A
NZ
[-0.198  5.427 45.077]
ASN
73
A
CG
[ 2.326  9.343 37.127]
TRP
74
A
CH2
[ 2.761  6.327 46.79 ]
GLU
75
A
CD
[ 2.38  15.513 38.757]
VAL
76
A
CG1
[-1.071 11.203 36.408]


In [13]:
def tmalign_structural_alignment(pdb_id_1, pdb_id_2):
    """TMAlign Structural Alignment
    Compare structural similarities between two PDB structures (regardless of the rotation)
    https://zhanggroup.org/TM-score/
    
    Parameters:
    pdb_id_1 (str): The PDB ID for the first protein structure
    pdb_id_2 (str): The PDB ID for the second protein structure
    
    Returns:
    float: The TMScore, a value between (0,1]. 1 indicates a perfect match. >0.5 is similar enough. <0.17 is two unrelated structures.
    
    """
    pdb_id_1_file_directory = dataset_directory + pdb_id_1.lower() + ".pdb"
    pdb_id_2_file_directory = dataset_directory + pdb_id_2.lower() + ".pdb"
    # Execute TMAlign
    tmalign_thread = subprocess.run(["./TMalign", pdb_id_1_file_directory, pdb_id_2_file_directory], capture_output=True, text=True)
    output_text = tmalign_thread.stdout

    # Retrieved TMScore from TMAlign results
    tmscore_raw_list = re.findall("TM-score=\s[0-9]+.[0-9]+", output_text)

    # Convert the TMScore into floats, then get the maximum TMScore
    tmscore_list = list(map(lambda x: float(re.sub("TM-score=\s", "", x)), tmscore_raw_list))
    max_tmscore = max(tmscore_list)
    return max_tmscore

tmscore = tmalign_structural_alignment("1AHW_l_u", "1BVK_l_u")
print(tmscore)

0.23652


In [14]:
# Given one receptor and one ligand, infer its interfaces
# The protein-protein interfaces is a list of Residue class
def get_interface(pdb_id_1, pdb_id_2, threshold=6.0):
    """Get Protein Interface
    Given one receptor structure and one ligand structure, infer its interfaces
    
    Parameters:
    pdb_id_1 (str): The PDB ID for the first protein structure
    pdb_id_2 (str): The PDB ID for the second protein structure
    threshold: The acceptable distance between a receptor's atom and a ligand's atom
    
    Returns:
    list: List of Residue object which constitutes the protein interface
    
    """
    interface_list = []
    pdb_1_structure = pdb_parser.get_structure(pdb_id_1, repository + "TMalign/" + pdb_id_1 + "_lha.pdb")
    pdb_2_structure = pdb_parser.get_structure(pdb_id_2, repository + "TMalign/" + pdb_id_2 + "_lha.pdb")
    for atom_1 in pdb_1_structure.get_atoms():
        print("Atom 1: " + atom_1.get_name())
        for atom_2 in pdb_2_structure.get_atoms():
            print("Atom 2: " + atom_2.get_name())
            current_distance = euclidean_distance(atom_1.get_coord(), atom_2.get_coord())
            if current_distance < threshold:
                # Create a new Residue instance
                current_residue_name = atom_1.get_parent().get_resname()
                current_residue_sequence_position = atom_1.get_parent().get_full_id()[3][1]
                current_chain_name = atom_1.get_parent().get_parent().id
                current_lha_name = atom_1.get_name()
                current_lha_coordinates = atom_1.get_coord()
                current_atom = Residue(current_residue_name,
                                       current_residue_sequence_position,
                                       current_chain_name,
                                       current_lha_name,
                                       current_lha_coordinates)
                interface_list.append(current_atom)
                break
    return interface_list
    
sample_interface_list = get_interface("3nos", "1pme")
print(sample_interface_list)
print(type(sample_interface_list))
print(len(sample_interface_list))

Atom 1: NZ
Atom 2: CA
Atom 2: CD
Atom 2: CG1
Atom 2: CZ
Atom 2: CG
Atom 2: CG1
Atom 2: CA
Atom 2: CG
Atom 2: CZ
Atom 2: OH
Atom 2: CG2
Atom 2: CG
Atom 2: CD1
Atom 2: OG
Atom 2: OH
Atom 2: CD1
Atom 2: CA
Atom 2: OH
Atom 2: CA
Atom 2: CE
Atom 2: CG1
Atom 2: SG
Atom 2: OG
Atom 2: CB
Atom 2: OH
Atom 2: CG
Atom 2: CG
Atom 2: CG1
Atom 2: CG
Atom 2: NZ
Atom 2: CG1
Atom 2: CZ
Atom 2: CG1
Atom 2: CB
Atom 2: CD1
Atom 2: NZ
Atom 2: NZ
Atom 2: CD1
Atom 2: OG
Atom 2: CG
Atom 2: CZ
Atom 2: CD
Atom 2: CE1
Atom 2: CD
Atom 2: CG2
Atom 2: OH
Atom 2: SG
Atom 2: CD
Atom 2: CZ
Atom 2: CG2
Atom 2: CD1
Atom 2: CZ
Atom 2: CD
Atom 2: CD1
Atom 2: NZ
Atom 2: CD1
Atom 2: CD1
Atom 2: CD1
Atom 2: CZ
Atom 2: CZ
Atom 2: CZ
Atom 2: CE1
Atom 2: CD
Atom 2: CG
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: CD1
Atom 2: CG
Atom 2: CG
Atom 2: CD1
Atom 2: CD1
Atom 2: CZ
Atom 2: CB
Atom 2: CG
Atom 2: CG2
Atom 2: CD1
Atom 2: CD
Atom 2: CD
Atom 2: CE
Atom 2: NZ
Atom 2: CG
Atom 2: CG1
Atom 2: OH
Atom 2: CD1
Atom 2: CG1
Atom 2: CG2
A

Atom 2: CD
Atom 2: OH
Atom 2: CG1
Atom 2: CB
Atom 2: CG2
Atom 2: CZ
Atom 2: CH2
Atom 2: OH
Atom 2: CZ
Atom 2: CB
Atom 2: CG
Atom 2: CD
Atom 2: CD1
Atom 2: CE
Atom 2: CD1
Atom 2: CG
Atom 2: OG
Atom 2: NZ
Atom 2: CA
Atom 2: OH
Atom 2: CG2
Atom 2: NZ
Atom 2: OG
Atom 2: CD1
Atom 2: CG
Atom 2: CD1
Atom 2: CH2
Atom 2: OG
Atom 2: CG1
Atom 2: CA
Atom 2: SG
Atom 2: CD1
Atom 2: CD1
Atom 2: CB
Atom 2: CD
Atom 2: CE
Atom 2: CD1
Atom 2: OG
Atom 2: CG
Atom 2: CZ
Atom 2: CG
Atom 2: CD1
Atom 2: CZ
Atom 2: CG
Atom 2: CA
Atom 2: NZ
Atom 2: CE1
Atom 2: OH
Atom 2: CD1
Atom 2: CG
Atom 2: CD
Atom 2: CD1
Atom 2: CG
Atom 2: CE1
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: OG
Atom 2: CG
Atom 2: OG
Atom 2: CD
Atom 2: CD
Atom 2: CG
Atom 2: CD1
Atom 2: CG
Atom 2: SG
Atom 2: CD1
Atom 2: CD1
Atom 2: CG
Atom 2: CD1
Atom 2: NZ
Atom 2: CB
Atom 2: CZ
Atom 2: CG
Atom 2: OH
Atom 2: CD1
Atom 2: CD1
Atom 2: OG
Atom 2: CD1
Atom 2: CG
Atom 2: CE1
Atom 2: NZ
Atom 2: CG
Atom 2: NZ
Atom 2: CG1
A

Atom 2: CA
Atom 2: OH
Atom 2: CZ
Atom 2: OG
Atom 1: CD
Atom 2: CA
Atom 2: CD
Atom 2: CG1
Atom 2: CZ
Atom 2: CG
Atom 2: CG1
Atom 2: CA
Atom 2: CG
Atom 2: CZ
Atom 2: OH
Atom 2: CG2
Atom 2: CG
Atom 2: CD1
Atom 2: OG
Atom 2: OH
Atom 2: CD1
Atom 2: CA
Atom 2: OH
Atom 2: CA
Atom 2: CE
Atom 2: CG1
Atom 2: SG
Atom 2: OG
Atom 2: CB
Atom 2: OH
Atom 2: CG
Atom 2: CG
Atom 2: CG1
Atom 2: CG
Atom 2: NZ
Atom 2: CG1
Atom 2: CZ
Atom 2: CG1
Atom 2: CB
Atom 2: CD1
Atom 2: NZ
Atom 2: NZ
Atom 2: CD1
Atom 2: OG
Atom 2: CG
Atom 2: CZ
Atom 2: CD
Atom 2: CE1
Atom 2: CD
Atom 2: CG2
Atom 2: OH
Atom 2: SG
Atom 2: CD
Atom 2: CZ
Atom 2: CG2
Atom 2: CD1
Atom 2: CZ
Atom 2: CD
Atom 2: CD1
Atom 2: NZ
Atom 2: CD1
Atom 2: CD1
Atom 2: CD1
Atom 2: CZ
Atom 2: CZ
Atom 2: CZ
Atom 2: CE1
Atom 2: CD
Atom 2: CG
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: CD1
Atom 2: CG
Atom 2: CG
Atom 2: CD1
Atom 2: CD1
Atom 2: CZ
Atom 2: CB
Atom 2: CG
Atom 2: CG2
Atom 2: CD1
Atom 2: CD
Atom 2: CD
Atom 2: CE
Atom 2: NZ
Atom 2: CG
Atom 2: CG1
Atom

Atom 2: CG
Atom 2: CE1
Atom 2: CG2
Atom 2: CA
Atom 2: CZ
Atom 2: CD1
Atom 2: CG2
Atom 2: CD
Atom 2: OH
Atom 2: CG1
Atom 2: CB
Atom 2: CG2
Atom 2: CZ
Atom 2: CH2
Atom 2: OH
Atom 2: CZ
Atom 2: CB
Atom 2: CG
Atom 2: CD
Atom 2: CD1
Atom 2: CE
Atom 2: CD1
Atom 2: CG
Atom 2: OG
Atom 2: NZ
Atom 2: CA
Atom 2: OH
Atom 2: CG2
Atom 2: NZ
Atom 2: OG
Atom 2: CD1
Atom 2: CG
Atom 2: CD1
Atom 2: CH2
Atom 2: OG
Atom 2: CG1
Atom 2: CA
Atom 2: SG
Atom 2: CD1
Atom 2: CD1
Atom 2: CB
Atom 2: CD
Atom 2: CE
Atom 2: CD1
Atom 2: OG
Atom 2: CG
Atom 2: CZ
Atom 2: CG
Atom 2: CD1
Atom 2: CZ
Atom 2: CG
Atom 2: CA
Atom 2: NZ
Atom 2: CE1
Atom 2: OH
Atom 2: CD1
Atom 2: CG
Atom 2: CD
Atom 2: CD1
Atom 2: CG
Atom 2: CE1
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: OG
Atom 2: CG
Atom 2: OG
Atom 2: CD
Atom 2: CD
Atom 2: CG
Atom 2: CD1
Atom 2: CG
Atom 2: SG
Atom 2: CD1
Atom 2: CD1
Atom 2: CG
Atom 2: CD1
Atom 2: NZ
Atom 2: CB
Atom 2: CZ
Atom 2: CG
Atom 2: OH
Atom 2: CD1
Atom 2: CD1
Atom 2: OG


Atom 2: CA
Atom 2: CZ
Atom 2: CD1
Atom 2: CG2
Atom 2: CD
Atom 2: OH
Atom 2: CG1
Atom 2: CB
Atom 2: CG2
Atom 2: CZ
Atom 2: CH2
Atom 2: OH
Atom 2: CZ
Atom 2: CB
Atom 2: CG
Atom 2: CD
Atom 2: CD1
Atom 2: CE
Atom 2: CD1
Atom 2: CG
Atom 2: OG
Atom 2: NZ
Atom 2: CA
Atom 2: OH
Atom 2: CG2
Atom 2: NZ
Atom 2: OG
Atom 2: CD1
Atom 2: CG
Atom 2: CD1
Atom 2: CH2
Atom 2: OG
Atom 2: CG1
Atom 2: CA
Atom 2: SG
Atom 2: CD1
Atom 2: CD1
Atom 2: CB
Atom 2: CD
Atom 2: CE
Atom 2: CD1
Atom 2: OG
Atom 2: CG
Atom 2: CZ
Atom 2: CG
Atom 2: CD1
Atom 2: CZ
Atom 2: CG
Atom 2: CA
Atom 2: NZ
Atom 2: CE1
Atom 2: OH
Atom 2: CD1
Atom 2: CG
Atom 2: CD
Atom 2: CD1
Atom 2: CG
Atom 2: CE1
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: OG
Atom 2: CG
Atom 2: OG
Atom 2: CD
Atom 2: CD
Atom 2: CG
Atom 2: CD1
Atom 2: CG
Atom 2: SG
Atom 2: CD1
Atom 2: CD1
Atom 2: CG
Atom 2: CD1
Atom 2: NZ
Atom 2: CB
Atom 2: CZ
Atom 2: CG
Atom 2: OH
Atom 2: CD1
Atom 2: CD1
Atom 2: OG
Atom 2: CD1
Atom 2: CG
Atom 2: CE1


...

Atom 2: NZ
Atom 2: CB
Atom 2: CZ
Atom 2: CG
Atom 2: OH
Atom 2: CD1
Atom 2: CD1
Atom 2: OG
Atom 2: CD1
Atom 2: CG
Atom 2: CE1
Atom 2: NZ
Atom 2: CG
Atom 2: NZ
Atom 2: CG1
Atom 2: CG
Atom 2: CH2
Atom 2: CG
Atom 2: CZ
Atom 2: CD1
Atom 2: CZ
Atom 2: CG
Atom 2: CG
Atom 2: CB
Atom 2: CG
Atom 2: OG
Atom 2: NZ
Atom 2: CB
Atom 2: CD1
Atom 2: CG
Atom 2: CD1
Atom 2: CD1
Atom 2: CG
Atom 2: NZ
Atom 2: CE
Atom 2: CD1
Atom 2: CG2
Atom 2: CZ
Atom 2: CG
Atom 2: CG
Atom 2: CE1
Atom 2: NZ
Atom 2: CZ
Atom 2: CD1
Atom 2: CD
Atom 2: CG1
Atom 2: CD
Atom 2: CD
Atom 2: CB
Atom 2: CD1
Atom 2: CB
Atom 2: CE1
Atom 2: CG
Atom 2: OH
Atom 2: CD1
Atom 2: CD
Atom 2: CD
Atom 2: OH
Atom 2: OH
Atom 2: CG
Atom 2: CG
Atom 2: OG
Atom 2: CG
Atom 2: CD
Atom 2: CG
Atom 2: CD1
Atom 2: CB
Atom 2: CD
Atom 2: CB
Atom 2: CG
Atom 2: CZ
Atom 2: CD1
Atom 2: CG
Atom 2: NZ
Atom 2: CD
Atom 2: NZ
Atom 2: CD1
Atom 2: NZ
Atom 2: CD
Atom 2: CD1
Atom 2: CD1
Atom 2: CZ
Atom 2: CD
Atom 2: CD
Atom 2: CG2
Atom 2: CB
Atom 2: CZ
Atom 2: CZ
Atom 2: 

Atom 2: CG2
Atom 2: CA
Atom 2: CZ
Atom 2: CD1
Atom 2: CG2
Atom 2: CD
Atom 2: OH
Atom 2: CG1
Atom 2: CB
Atom 2: CG2
Atom 2: CZ
Atom 2: CH2
Atom 2: OH
Atom 2: CZ
Atom 2: CB
Atom 2: CG
Atom 2: CD
Atom 2: CD1
Atom 2: CE
Atom 2: CD1
Atom 2: CG
Atom 2: OG
Atom 2: NZ
Atom 2: CA
Atom 2: OH
Atom 2: CG2
Atom 2: NZ
Atom 2: OG
Atom 2: CD1
Atom 2: CG
Atom 2: CD1
Atom 2: CH2
Atom 2: OG
Atom 2: CG1
Atom 2: CA
Atom 2: SG
Atom 2: CD1
Atom 2: CD1
Atom 2: CB
Atom 2: CD
Atom 2: CE
Atom 2: CD1
Atom 2: OG
Atom 2: CG
Atom 2: CZ
Atom 2: CG
Atom 2: CD1
Atom 2: CZ
Atom 2: CG
Atom 2: CA
Atom 2: NZ
Atom 2: CE1
Atom 2: OH
Atom 2: CD1
Atom 2: CG
Atom 2: CD
Atom 2: CD1
Atom 2: CG
Atom 2: CE1
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: OG
Atom 2: CG
Atom 2: OG
Atom 2: CD
Atom 2: CD
Atom 2: CG
Atom 2: CD1
Atom 2: CG
Atom 2: SG
Atom 2: CD1
Atom 2: CD1
Atom 2: CG
Atom 2: CD1
Atom 2: NZ
Atom 2: CB
Atom 2: CZ
Atom 2: CG
Atom 2: OH
Atom 2: CD1
Atom 2: CD1
Atom 2: OG
Atom 2: CD1
Atom 2: CG


Atom 2: CZ
Atom 2: CZ
Atom 2: CD
Atom 2: CG
Atom 2: CA
Atom 2: OH
Atom 2: CZ
Atom 2: OG
Atom 1: CG1
Atom 2: CA
Atom 2: CD
Atom 2: CG1
Atom 2: CZ
Atom 2: CG
Atom 2: CG1
Atom 2: CA
Atom 2: CG
Atom 2: CZ
Atom 2: OH
Atom 2: CG2
Atom 2: CG
Atom 2: CD1
Atom 2: OG
Atom 2: OH
Atom 2: CD1
Atom 2: CA
Atom 2: OH
Atom 2: CA
Atom 2: CE
Atom 2: CG1
Atom 2: SG
Atom 2: OG
Atom 2: CB
Atom 2: OH
Atom 2: CG
Atom 2: CG
Atom 2: CG1
Atom 2: CG
Atom 2: NZ
Atom 2: CG1
Atom 2: CZ
Atom 2: CG1
Atom 2: CB
Atom 2: CD1
Atom 2: NZ
Atom 2: NZ
Atom 2: CD1
Atom 2: OG
Atom 2: CG
Atom 2: CZ
Atom 2: CD
Atom 2: CE1
Atom 2: CD
Atom 2: CG2
Atom 2: OH
Atom 2: SG
Atom 2: CD
Atom 2: CZ
Atom 2: CG2
Atom 2: CD1
Atom 2: CZ
Atom 2: CD
Atom 2: CD1
Atom 2: NZ
Atom 2: CD1
Atom 2: CD1
Atom 2: CD1
Atom 2: CZ
Atom 2: CZ
Atom 2: CZ
Atom 2: CE1
Atom 2: CD
Atom 2: CG
Atom 2: CD1
Atom 2: CD1
Atom 2: CA
Atom 2: CD1
Atom 2: CG
Atom 2: CG
Atom 2: CD1
Atom 2: CD1
Atom 2: CZ
Atom 2: CB
Atom 2: CG
Atom 2: CG2
Atom 2: CD1
Atom 2: CD
Atom 2: CD
Atom

Atom 2: CD1
Atom 2: CE1
Atom 2: CZ
Atom 2: CG
Atom 2: CD1
Atom 2: NZ
Atom 2: CG
Atom 2: OG
Atom 2: CG
Atom 2: CD1
Atom 2: CD1
Atom 2: CD1
Atom 2: CG
Atom 2: CG2
Atom 2: CG2
Atom 2: CG
Atom 2: CD1
Atom 2: NZ
Atom 2: CD1
Atom 2: SG
Atom 2: CG
Atom 2: CZ
Atom 2: CA
Atom 2: CD1
Atom 2: CB
Atom 2: CZ
Atom 2: CG1
Atom 2: CB
Atom 2: CG
Atom 2: CG
Atom 2: CG
Atom 2: CE1
Atom 2: CG
Atom 2: CE1
Atom 2: CG2
Atom 2: CA
Atom 2: CZ
Atom 2: CD1
Atom 2: CG2
Atom 2: CD
Atom 2: OH
Atom 2: CG1
Atom 2: CB
Atom 2: CG2
Atom 2: CZ
Atom 2: CH2
Atom 2: OH
Atom 2: CZ
Atom 2: CB
Atom 2: CG
Atom 2: CD
Atom 2: CD1
Atom 2: CE
Atom 2: CD1
Atom 2: CG
Atom 2: OG
Atom 2: NZ
Atom 2: CA
Atom 2: OH
Atom 2: CG2
Atom 2: NZ
Atom 2: OG
Atom 2: CD1
Atom 2: CG
Atom 2: CD1
Atom 2: CH2
Atom 2: OG
Atom 2: CG1
Atom 2: CA
Atom 2: SG
Atom 2: CD1
Atom 2: CD1
Atom 2: CB
Atom 2: CD
Atom 2: CE
Atom 2: CD1
Atom 2: OG
Atom 2: CG
Atom 2: CZ
Atom 2: CG
Atom 2: CD1
Atom 2: CZ
Atom 2: CG
Atom 2: CA
Atom 2: NZ
Atom 2: CE1
Atom 2: OH
Atom 2: CD1

Atom 2: CD1
Atom 2: CA
Atom 2: CD1
Atom 2: CG
Atom 2: CG
Atom 2: CD1
Atom 2: CD1
Atom 2: CZ
Atom 2: CB
Atom 2: CG
Atom 2: CG2
Atom 2: CD1
Atom 2: CD
Atom 2: CD
Atom 2: CE
Atom 2: NZ
Atom 2: CG
Atom 2: CG1
Atom 2: OH
Atom 2: CD1
Atom 2: CG1
Atom 2: CG2
Atom 2: CE1
Atom 2: CD1
Atom 2: CE
Atom 2: CA
Atom 2: CB
Atom 2: CG
Atom 2: CD1
Atom 2: OH
Atom 2: NZ
Atom 2: CD1
Atom 2: CD1
Atom 2: NZ
Atom 2: CG2
Atom 2: CD
Atom 2: CE1
Atom 2: CD1
Atom 2: OG
Atom 2: CG
Atom 2: CG
Atom 2: CE1
Atom 2: CD1
Atom 2: SG
Atom 2: OH
Atom 2: CZ
Atom 2: CD1
Atom 2: OH
Atom 2: CD
Atom 2: CD1
Atom 2: CD1
Atom 2: CZ
Atom 2: CA
Atom 2: CD1
Atom 2: NZ
Atom 2: OH
Atom 2: CD1
Atom 2: CE1
Atom 2: OG
Atom 2: CB
Atom 2: CG
Atom 2: CG1
Atom 2: CD1
Atom 2: CE1
Atom 2: CZ
Atom 2: CG
Atom 2: CD1
Atom 2: NZ
Atom 2: CG
Atom 2: OG
Atom 2: CG
Atom 2: CD1
Atom 2: CD1
Atom 2: CD1
Atom 2: CG
Atom 2: CG2
Atom 2: CG2
Atom 2: CG
Atom 2: CD1
Atom 2: NZ
Atom 2: CD1
Atom 2: SG
Atom 2: CG
Atom 2: CZ
Atom 2: CA
Atom 2: CD1
Atom 2: CB
Atom 

In [ ]:
def gass_ppi()

## Section 1: Proof-of-Concept

In [6]:
# Query Protein
input_pdb_id = "1AHW_r_u"

# Step 1: Find the structural neighbour of the query protein using TMAlign Structural Alignment

# Remove the first element in this case, since it's the input_pdb_id
dataset_list = dbd5_aa_r_list[1:]

tmscore_list = list(map(lambda x: tmalign_structural_alignment(input_pdb_id, x), dataset_list))
print(tmscore_list) 
maximum_index = np.argmax(tmscore_list)
print(dataset_list[maximum_index])

# Step 2: Find the interface of the structural neighbour, then use it as the template


[0.96368, 0.71974, 0.89282, 0.96941, 0.86854, 0.96954, 0.66046, 0.85705, 0.76904, 0.79738, 0.66313, 0.45949, 0.71285, 0.96372, 0.97342, 0.96571, 0.95849, 0.70099, 0.66768, 0.49131, 0.79083, 0.68356, 0.60908, 0.64004, 0.953, 0.51087, 0.8124]
3MXW_r_u
